In [1]:
from collections import OrderedDict

from Sastrawi.Stemmer.StemmerFactory import StemmerFactory
from Sastrawi.StopWordRemover.StopWordRemoverFactory import StopWordRemoverFactory
from math import log10, sqrt
import glob
import urllib.request

from bs4 import BeautifulSoup
import tqdm



factory = StemmerFactory()
stemmer = factory.create_stemmer()
stopwords_factory = StopWordRemoverFactory()
stopwords = stopwords_factory.get_stop_words()

ModuleNotFoundError: No module named 'Sastrawi'

In [21]:
def give_path(fld_path):                             #give path of the folder containing all documents
    dic = {}
    file_names = glob.glob(fld_path)
    files_150 = file_names
    for file in files_150:
        name = file.split('/')[-1]
        with open(file, 'r', errors='ignore') as f:
            data = f.read()
        dic[name] = data
    return dic

In [22]:
path = 'dataklasifikasitxt/*.txt'
docs = give_path(path)
print("\nDocument Length ", len(docs))
# print(docs)


Document Length  78


In [23]:
# def get_list_of_word(list_of_document, stopword):
#     list_of_word = []
#     for sentence in list_of_document.values():
#         for word in sentence.split(" "):
#             stemmed_word = stemmer.stem(word)
#             if word not in stopword and stemmed_word not in list_of_word:
#                 list_of_word.append(stemmed_word)
#     return list_of_word

In [24]:
# list_of_word = get_list_of_word(docs, stopwords)
# print(len(list_of_word))

In [25]:
# save list of word on txt

datapath = 'datatxt/list_of_word.txt'

# write to txt
# with open(datapath, 'w') as filehandle:
#     filehandle.write(str(list_of_word))
# datatotxt = ''
# for i in range(len(list_of_word)):
#     if i > 0 :
#         datatotxt += ','
#     datatotxt += list_of_word[i]

# with open(datapath, 'w') as filehandle:
#     filehandle.write(datatotxt)

# read to txt
data_file_names = glob.glob(datapath)
with open(datapath, 'r', errors='ignore') as f:
    data = f.read()

list_of_word = []
list_of_word = data.split(',')


print(len(list_of_word))



1788


In [26]:
def stateForQueryExpansion(kata_kunci):
    
    words = []
    thesaurus = {}
    words_result = ''

    for word in kata_kunci.split(" "):
            stemmed_word = stemmer.stem(word)
            if word not in stopwords and stemmed_word not in words:
                words.append(stemmed_word)

    # print(words)
    words = list(set(words))
    for x in words:
        name = x
        data = {"q": name}
        encoded_data = urllib.parse.urlencode(data).encode("utf-8")
        content = urllib.request.urlopen("http://sinonimkata.com/search.php", encoded_data)
        soup = BeautifulSoup(content, 'html.parser')

        # print(x)

        # print(soup.find_all('a', {'rel': 'nofollow'}))
        words_result += x+' '
        try:

            for x in soup.find('td', {'width': '90%'}).find_all('a', {'rel': 'nofollow'}):
                # print(x.get_text())
                words_result += x.get_text()+' '

            synonym = soup.find('td', attrs={'width': '90%'}).find_all('a')
            synonym = [x.gettext() for x in synonym]

            thesaurus[x] = [x] + synonym

        except:
            thesaurus[x] = [name]

    return words_result

In [27]:
user_kata_kunci = "pembelajaran tatap muka dan jarak jauh"
print('Kata Kunci before QE : ', user_kata_kunci)

user_kata_kunci = stateForQueryExpansion(user_kata_kunci)
print('Kata Kunci after QE : ', user_kata_kunci)

kata_kunci = ''
for index, word in enumerate(user_kata_kunci.split(" ")):
            stemmed_word = stemmer.stem(word)
            if word not in stopwords and stemmed_word not in kata_kunci:
                if index > 0 :
                    kata_kunci += ' '
                kata_kunci += stemmed_word

print('Kata Kunci after Stemm : ', kata_kunci)

# word_of_query = []
# for index, word in enumerate(kata_kunci.split(" ")):
#             if word not in list_of_word:
#                 word_of_query.append(word)
# print(word_of_query)


print('Length List Of Word Before :  ',len(list_of_word))
print('Length Docs Before :  ',len(docs))

word_of_query = []
# for index, word in enumerate(kata_kunci.split(" ")):
#             stemmed_word = stemmer.stem(word)
#             print(word)
#             if word not in stopwords and stemmed_word not in word_of_query:
#                 word_of_query.append(word)

for word in kata_kunci.split(" "):
    # print(word)
    if word not in list_of_word:
        word_of_query.append(word)
        
print(word_of_query)
list_of_word = word_of_query + list_of_word
print('Length List Of Word After :  ',len(list_of_word))

query_docs = {}
query_docs['kata_kunci'] = kata_kunci
docs = {**query_docs,**docs}
print('Length docs After :  ',len(docs))
    


Kata Kunci before QE :  pembelajaran tatap muka dan jarak jauh
Kata Kunci after QE :  muka bagian depan bidang dada depan durja front hadapan halaman kaca lembaran paras pendahuluan permukaan permulaan roman rupa sadar sebelah hadapan segi sisi sosok syatar tampang wajah ajar open unfastened jauh tatap lihat jarak antara jangka jeda kesenjangan langkah lat renggang ruang sela selang (waktu) senggang tenggang tengka yojana menjarakkan  memisahkan menjauhkan merenggangkan 
Kata Kunci after Stemm :  muka bagi depan bidang dada durja front hadap halaman kaca lembar paras dahulu mula roman rupa sadar belah segi sisi sosok syatar tampang wajah ajar open unfastened jauh tatap lihat jarak jangka jeda senjang langkah lat renggang ruang sela selang waktu senggang tenggang tengka yojana pisah
Length List Of Word Before :   1788
Length Docs Before :   78
['bidang', 'dada', 'durja', 'front', 'halaman', 'kaca', 'lembar', 'paras', 'dahulu', 'mula', 'roman', 'sadar', 'belah', 'segi', 'syatar', 'tampan

In [28]:
def create_term_frequency(list_of_word, length_of_document_with_kk):
    term_frequency = []
    for _ in range(length_of_document_with_kk):
        term_frequency.append(dict(zip(list_of_word, [0 for _ in range(len(list_of_word))])))
    return term_frequency

term_frequency = create_term_frequency(list_of_word, len(docs))
for index, sentence in enumerate(docs.values()):
    for word in stemmer.stem(sentence).split(" "):
        if word in term_frequency[index]:
            term_frequency[index][word] += 1
print(term_frequency)


[{'bidang': 1, 'dada': 1, 'durja': 1, 'front': 1, 'halaman': 1, 'kaca': 1, 'lembar': 1, 'paras': 1, 'dahulu': 1, 'mula': 1, 'roman': 1, 'sadar': 1, 'belah': 1, 'segi': 1, 'syatar': 1, 'tampang': 1, 'wajah': 1, 'open': 1, 'unfastened': 1, 'lat': 1, 'renggang': 1, 'sela': 1, 'selang': 1, 'senggang': 1, 'tenggang': 1, 'tengka': 1, 'yojana': 1, 'pandemi': 0, 'belum': 0, 'reda': 0, 'tetap': 0, 'prioritas': 0, 'penting': 0, 'anak anak': 0, 'masa': 0, 'milik': 0, 'rentan': 0, 'tinggi': 0, 'baik': 0, 'sisi': 1, 'sehat': 0, 'maupun': 0, 'hidup': 0, 'sosial selain': 0, 'tingkat': 0, 'infeksi': 0, 'mati': 0, 'anak': 0, 'kasus': 0, 'covid-19': 0, 'indonesia': 0, 'golong': 0, 'dapat': 0, 'situasi': 0, 'riskan': 0, 'jumlah': 0, 'kerja': 0, 'malnutrisi': 0, 'putus': 0, 'sekolah mari': 0, 'aman': 0, 'selamat': 0, 'pasti': 0, 'segala': 0, 'aktivitas': 0, 'pakaimasker': 0, 'jagajarak': 0, 'cucitanganpakaisabun baca': 0, 'pandu': 0, 'https s id lindungi-anak': 0, 'ajar': 1, 'jarak': 1, 'jauh': 1, 'pjj': 

In [29]:
term_frequency = create_term_frequency(list_of_word, len(docs))
for index, sentence in enumerate(docs.values()):
    for word in stemmer.stem(sentence).split(" "):
        if word in term_frequency[index]:
            term_frequency[index][word] += 1
print(term_frequency)

[{'bidang': 1, 'dada': 1, 'durja': 1, 'front': 1, 'halaman': 1, 'kaca': 1, 'lembar': 1, 'paras': 1, 'dahulu': 1, 'mula': 1, 'roman': 1, 'sadar': 1, 'belah': 1, 'segi': 1, 'syatar': 1, 'tampang': 1, 'wajah': 1, 'open': 1, 'unfastened': 1, 'lat': 1, 'renggang': 1, 'sela': 1, 'selang': 1, 'senggang': 1, 'tenggang': 1, 'tengka': 1, 'yojana': 1, 'pandemi': 0, 'belum': 0, 'reda': 0, 'tetap': 0, 'prioritas': 0, 'penting': 0, 'anak anak': 0, 'masa': 0, 'milik': 0, 'rentan': 0, 'tinggi': 0, 'baik': 0, 'sisi': 1, 'sehat': 0, 'maupun': 0, 'hidup': 0, 'sosial selain': 0, 'tingkat': 0, 'infeksi': 0, 'mati': 0, 'anak': 0, 'kasus': 0, 'covid-19': 0, 'indonesia': 0, 'golong': 0, 'dapat': 0, 'situasi': 0, 'riskan': 0, 'jumlah': 0, 'kerja': 0, 'malnutrisi': 0, 'putus': 0, 'sekolah mari': 0, 'aman': 0, 'selamat': 0, 'pasti': 0, 'segala': 0, 'aktivitas': 0, 'pakaimasker': 0, 'jagajarak': 0, 'cucitanganpakaisabun baca': 0, 'pandu': 0, 'https s id lindungi-anak': 0, 'ajar': 1, 'jarak': 1, 'jauh': 1, 'pjj': 

In [30]:
def create_document_frequency(list_of_word):
    return dict(zip(list_of_word, [0 for _ in range(len(list_of_word))]))

document_frequency = create_document_frequency(list_of_word)
for index, sentence in enumerate(term_frequency):
    # print(index, sentence)
    if index > 0:
        for key, value in sentence.items():
            if value:
                document_frequency[key] += 1

print(document_frequency)

{'bidang': 0, 'dada': 0, 'durja': 0, 'front': 0, 'halaman': 0, 'kaca': 0, 'lembar': 0, 'paras': 0, 'dahulu': 1, 'mula': 0, 'roman': 0, 'sadar': 0, 'belah': 0, 'segi': 0, 'syatar': 0, 'tampang': 0, 'wajah': 0, 'open': 0, 'unfastened': 0, 'lat': 0, 'renggang': 0, 'sela': 0, 'selang': 0, 'senggang': 0, 'tenggang': 0, 'tengka': 0, 'yojana': 0, 'pandemi': 39, 'belum': 19, 'reda': 1, 'tetap': 29, 'prioritas': 6, 'penting': 14, 'anak anak': 0, 'masa': 25, 'milik': 8, 'rentan': 4, 'tinggi': 10, 'baik': 15, 'sisi': 6, 'sehat': 45, 'maupun': 12, 'hidup': 3, 'sosial selain': 0, 'tingkat': 13, 'infeksi': 7, 'mati': 4, 'anak': 25, 'kasus': 4, 'covid-19': 56, 'indonesia': 28, 'golong': 1, 'dapat': 39, 'situasi': 10, 'riskan': 1, 'jumlah': 13, 'kerja': 7, 'malnutrisi': 1, 'putus': 5, 'sekolah mari': 0, 'aman': 21, 'selamat': 17, 'pasti': 14, 'segala': 1, 'aktivitas': 6, 'pakaimasker': 7, 'jagajarak': 3, 'cucitanganpakaisabun baca': 0, 'pandu': 18, 'https s id lindungi-anak': 0, 'ajar': 26, 'jarak': 1

In [31]:
def get_d_df(length_of_document, document_frequency):
    d_df = {}
    for key, value in document_frequency.items():
        try:
            d_df[key] = round((length_of_document / value), 3)
        except:
            d_df[key] = 0

        print(f"{key} =  {length_of_document} / {value} = {d_df[key]}")
    return d_df

d_df = get_d_df(len(docs)-1, document_frequency)
# print(d_df)

bidang =  78 / 0 = 0
dada =  78 / 0 = 0
durja =  78 / 0 = 0
front =  78 / 0 = 0
halaman =  78 / 0 = 0
kaca =  78 / 0 = 0
lembar =  78 / 0 = 0
paras =  78 / 0 = 0
dahulu =  78 / 1 = 78.0
mula =  78 / 0 = 0
roman =  78 / 0 = 0
sadar =  78 / 0 = 0
belah =  78 / 0 = 0
segi =  78 / 0 = 0
syatar =  78 / 0 = 0
tampang =  78 / 0 = 0
wajah =  78 / 0 = 0
open =  78 / 0 = 0
unfastened =  78 / 0 = 0
lat =  78 / 0 = 0
renggang =  78 / 0 = 0
sela =  78 / 0 = 0
selang =  78 / 0 = 0
senggang =  78 / 0 = 0
tenggang =  78 / 0 = 0
tengka =  78 / 0 = 0
yojana =  78 / 0 = 0
pandemi =  78 / 39 = 2.0
belum =  78 / 19 = 4.105
reda =  78 / 1 = 78.0
tetap =  78 / 29 = 2.69
prioritas =  78 / 6 = 13.0
penting =  78 / 14 = 5.571
anak anak =  78 / 0 = 0
masa =  78 / 25 = 3.12
milik =  78 / 8 = 9.75
rentan =  78 / 4 = 19.5
tinggi =  78 / 10 = 7.8
baik =  78 / 15 = 5.2
sisi =  78 / 6 = 13.0
sehat =  78 / 45 = 1.733
maupun =  78 / 12 = 6.5
hidup =  78 / 3 = 26.0
sosial selain =  78 / 0 = 0
tingkat =  78 / 13 = 6.0
inf

In [32]:
def get_idf(d_df):
    idf = {}
    for key, value in d_df.items():
        try:
            idf[key] = round(log10(value), 3)
        except:
            idf[key] = 0

    return idf

idf = get_idf(d_df)
print(idf)

{'bidang': 0, 'dada': 0, 'durja': 0, 'front': 0, 'halaman': 0, 'kaca': 0, 'lembar': 0, 'paras': 0, 'dahulu': 1.892, 'mula': 0, 'roman': 0, 'sadar': 0, 'belah': 0, 'segi': 0, 'syatar': 0, 'tampang': 0, 'wajah': 0, 'open': 0, 'unfastened': 0, 'lat': 0, 'renggang': 0, 'sela': 0, 'selang': 0, 'senggang': 0, 'tenggang': 0, 'tengka': 0, 'yojana': 0, 'pandemi': 0.301, 'belum': 0.613, 'reda': 1.892, 'tetap': 0.43, 'prioritas': 1.114, 'penting': 0.746, 'anak anak': 0, 'masa': 0.494, 'milik': 0.989, 'rentan': 1.29, 'tinggi': 0.892, 'baik': 0.716, 'sisi': 1.114, 'sehat': 0.239, 'maupun': 0.813, 'hidup': 1.415, 'sosial selain': 0, 'tingkat': 0.778, 'infeksi': 1.047, 'mati': 1.29, 'anak': 0.494, 'kasus': 1.29, 'covid-19': 0.144, 'indonesia': 0.445, 'golong': 1.892, 'dapat': 0.301, 'situasi': 0.892, 'riskan': 1.892, 'jumlah': 0.778, 'kerja': 1.047, 'malnutrisi': 1.892, 'putus': 1.193, 'sekolah mari': 0, 'aman': 0.57, 'selamat': 0.662, 'pasti': 0.746, 'segala': 1.892, 'aktivitas': 1.114, 'pakaimasker

In [33]:
def get_w_q_t(term_frequency, idf):
    w_q_t = []
    frekuensi_max = 2
    for index, document in enumerate(term_frequency):
        w_q_t.append({})

        for key, value in document.items():
            if index == 0:
                w_q_t[index][key] = (value/frekuensi_max) * idf[key]
            else:
                w_q_t[index][key] = value * idf[key]

    return w_q_t
    
w_q_t = get_w_q_t(term_frequency, idf)
print(w_q_t)

[{'bidang': 0.0, 'dada': 0.0, 'durja': 0.0, 'front': 0.0, 'halaman': 0.0, 'kaca': 0.0, 'lembar': 0.0, 'paras': 0.0, 'dahulu': 0.946, 'mula': 0.0, 'roman': 0.0, 'sadar': 0.0, 'belah': 0.0, 'segi': 0.0, 'syatar': 0.0, 'tampang': 0.0, 'wajah': 0.0, 'open': 0.0, 'unfastened': 0.0, 'lat': 0.0, 'renggang': 0.0, 'sela': 0.0, 'selang': 0.0, 'senggang': 0.0, 'tenggang': 0.0, 'tengka': 0.0, 'yojana': 0.0, 'pandemi': 0.0, 'belum': 0.0, 'reda': 0.0, 'tetap': 0.0, 'prioritas': 0.0, 'penting': 0.0, 'anak anak': 0.0, 'masa': 0.0, 'milik': 0.0, 'rentan': 0.0, 'tinggi': 0.0, 'baik': 0.0, 'sisi': 0.557, 'sehat': 0.0, 'maupun': 0.0, 'hidup': 0.0, 'sosial selain': 0.0, 'tingkat': 0.0, 'infeksi': 0.0, 'mati': 0.0, 'anak': 0.0, 'kasus': 0.0, 'covid-19': 0.0, 'indonesia': 0.0, 'golong': 0.0, 'dapat': 0.0, 'situasi': 0.0, 'riskan': 0.0, 'jumlah': 0.0, 'kerja': 0.0, 'malnutrisi': 0.0, 'putus': 0.0, 'sekolah mari': 0.0, 'aman': 0.0, 'selamat': 0.0, 'pasti': 0.0, 'segala': 0.0, 'aktivitas': 0.0, 'pakaimasker': 0

In [34]:
def get_q_d(w_q_t):
    q_d = []
    for index, document in enumerate(w_q_t):
        q_d.append({})
        total = 0
        for key, value in document.items():
            q_d[index][key] = round(value ** 2, 3)
            total += q_d[index][key]
        q_d[index]["total"] = round(sqrt(total), 3)
    return q_d

q_d = get_q_d(w_q_t)
print("Q/D WQT dipangkatkn 2 dan diakar")
for x in q_d:
    print(x['total'])

Q/D WQT dipangkatkn 2 dan diakar
3.124
8.491
8.726
11.319
13.754
9.365
10.758
6.61
7.06
10.614
26.348
9.832
8.405
8.54
5.885
12.967
16.209
21.488
16.31
9.371
11.661
6.755
11.128
11.244
14.476
36.324
9.818
10.745
9.997
24.775
9.758
11.042
17.373
12.453
15.428
10.99
11.745
13.772
18.056
10.511
8.676
13.433
10.642
9.716
8.308
9.344
6.579
5.936
8.51
46.002
24.494
12.28
6.755
7.661
12.248
16.13
27.38
41.41
53.555
10.854
8.51
10.71
10.154
12.248
6.686
24.097
17.71
34.902
28.572
8.155
6.981
10.134
4.92
6.715
10.192
9.584
21.737
26.807
11.988


In [35]:
def get_dj_q(tfidf):
    dj_q = []
    for index, document in enumerate(tfidf):
        dj_q.append({})
        total = 0
        for key, value in document.items():
            if index > 0:
                dj_q[index][key] = value * tfidf[0][key]
                total += dj_q[index][key]
            dj_q[index]["total"] = round(sqrt(total), 3)
    return dj_q

print("\nPerhitungan Sum (tfidf * tfidf_query) atau dj.q")
sum_dj_q = get_dj_q(w_q_t)
for x in sum_dj_q:
    print(x['total'])


Perhitungan Sum (tfidf * tfidf_query) atau dj.q
0.0
0.788
1.424
1.03
0.403
1.759
1.7
0.0
0.403
0.702
0.0
0.0
0.0
0.477
0.0
0.0
0.813
0.99
0.0
1.733
0.663
0.0
1.122
0.0
0.975
2.112
0.0
1.265
0.0
1.953
0.0
0.0
0.788
1.828
1.337
1.337
2.037
1.535
0.57
0.941
0.337
0.403
0.575
0.528
1.531
0.528
0.0
0.403
0.477
1.991
1.511
0.0
0.0
0.0
0.921
0.403
3.107
1.804
2.69
1.7
0.477
0.878
0.0
0.921
0.975
0.698
1.553
2.326
0.663
1.486
0.584
0.0
0.0
0.584
0.0
0.0
1.696
0.81
0.0


In [36]:
def get_sum_of_qd(q_d):
    sum_qd = []
    for index, document in enumerate(q_d):
        sum_qd.append({})
        total = 0
        for key, value in document.items():
            if index > 0:
                sum_qd[index][key] = value * q_d[0][key]
                total += sum_qd[index][key]
            sum_qd[index]["total"] = round(sqrt(total), 3)
    return sum_qd

print("\nPerhitungan |dj|.|q| (jarak dokumen * jarak query)")
sum_qd = get_sum_of_qd(q_d)
for x in sum_qd:
    print(x['total'])


Perhitungan |dj|.|q| (jarak dokumen * jarak query)
0.0
5.188
5.36
5.995
6.557
5.645
6.066
4.544
4.699
5.77
9.073
5.542
5.124
5.17
4.288
6.365
7.147
8.225
7.138
5.708
6.052
4.594
5.936
5.927
6.761
11.009
5.538
5.851
5.588
8.955
5.521
5.873
7.393
6.391
7.019
5.95
6.343
6.713
7.517
5.75
5.207
6.48
5.775
5.516
5.419
5.41
4.534
4.309
5.161
12.176
8.839
6.194
4.594
4.892
6.221
7.1
10.738
11.559
13.319
6.091
5.161
5.81
5.632
6.221
4.603
8.69
7.676
10.837
9.458
5.215
4.682
5.627
3.92
4.593
5.643
5.472
8.347
9.163
6.12


In [37]:
def get_sim(sumtfidf, sumqd):
    sim = []
    for index, document in enumerate(sumtfidf):
        sim.append({})
        if index > 0 :
            # print(sumtfidf[index]['total'],sumqd[index]['total'])
            # sim[index] = round((sumtfidf[index]['total']/sumqd[index]['total'])*2,3) if sumqd[index]['total'] != 0 else 0
            sim[index] = round((sumtfidf[index]['total']/sumqd[index]['total']),3) if sumqd[index]['total'] != 0 else 0

    return  sim

kesimpulan = {}
print("Perhitungan dj.q / |dj|.|q|")
sim = get_sim(sum_dj_q, sum_qd)

i = 0
for x in docs.keys():
    # print(x)
    if x != 'kata_kunci':
        kesimpulan[x] = sim[i]
    i += 1


Perhitungan dj.q / |dj|.|q|


In [38]:
sorted_value = OrderedDict(sorted(kesimpulan.items(), key=lambda x: x[1], reverse=True))

i = 1
for x in sorted_value:
    if kesimpulan[x] > 0 :
        print(i, x, kesimpulan[x])
    i += 1

1 doc_guru_dan_siswa_7.txt 0.321
2 doc_guru_dan_siswa_17.txt 0.312
3 doc_guru_dan_siswa_11.txt 0.304
4 doc_vaksin_1.txt 0.289
5 doc_guru_dan_siswa_1.txt 0.286
6 doc_guru_dan_siswa_18.txt 0.285
7 doc_ibu_dan_anak_6.txt 0.283
8 doc_ibu_dan_anak_16.txt 0.28
9 doc_guru_dan_siswa_21.txt 0.279
10 doc_guru_dan_siswa_16.txt 0.266
11 doc_guru_dan_siswa_6.txt 0.229
12 doc_guru_dan_siswa_5.txt 0.225
13 doc_guru_dan_siswa_2.txt 0.218
14 doc_guru_dan_siswa_12.txt 0.216
15 doc_vaksin_13.txt 0.215
16 doc_guru_dan_siswa_19.txt 0.212
17 doc_vaksin_10.txt 0.203
18 doc_vaksin_16.txt 0.202
19 doc_vaksin_12.txt 0.202
20 doc_vaksin_25.txt 0.192
21 doc_guru_dan_siswa_4.txt 0.19
22 doc_guru_dan_siswa_13.txt 0.189
23 doc_vaksin_21.txt 0.172
24 doc_vaksin_15.txt 0.171
25 doc_guru_dan_siswa_8.txt 0.164
26 doc_vaksin_2.txt 0.164
27 doc_vaksin_17.txt 0.156
28 doc_ibu_dan_anak_17.txt 0.152
29 doc_ibu_dan_anak_24.txt 0.151
30 doc_ibu_dan_anak_21.txt 0.148
31 doc_guru_dan_siswa_25.txt 0.148
32 doc_vaksin_24.txt 0.144